# IBM Applied Data Science Capstone by Coursera
### Week 5 Final Report
**_Opening a cafe in Singapore_**
- Build a dataframe of train stations in Singapore by web scraping the data from Wikipedia page
- Get the geographical coordinates of the stations
- Obtain the venue data for the neighborhoods around the stations from Foursquare API
- Explore and cluster the neighborhoods
- Select the best cluster to open a new cafe

#1. Initializing (Load the required modules)

In [0]:
#import libraries

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

!pip install foursquare
import foursquare

import json # library to handle JSON files

!pip install geocoder
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder #to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

import regex as re

print("Libraries imported.")

     |████████████████████████████████| 102kB 3.1MB/s 
Libraries imported.


#2. Find the list of train stations in Singapore by web-scraping

In [0]:
import pandas as pd

#Scrap data from Wikipedia page into a DataFrame

# send the GET request
from bs4 import BeautifulSoup
import requests
BASE_URL = "https://en.m.wikipedia.org/wiki/List_of_Singapore_MRT_stations"

stations = []
neighborhoodList = []

html = requests.get(BASE_URL).text
soup = BeautifulSoup(html, "html.parser")

In [0]:
#get data by web scraping with BeautifulSoup

neighborhoodList = []

contentTable = soup.find('table', {"class": "wikitable"})
trs = contentTable.find_all('tr')

for tr in trs:
    tds = tr.find_all('td')
    for td in tds:
        if tds.index(td) == 2:
            #print(td.get_text())
            neighborhoodList.append(td.text.strip())

In [0]:
sg_df = pd.DataFrame({"Neighborhood": neighborhoodList})
sg_df.head()

Neighborhood
0    Jurong East
1    Bukit Batok
2   Bukit Gombak
3      Brickland
4  Choa Chu Kang

In [0]:
#sg_df
sg_df.tail()

Neighborhood
222  Serangoon North
223        Tavistock
224       Ang Mo Kio
225        Teck Ghee
226      Bright Hill

In [0]:
#save DataFrame as CSV file, and then read it to check the formatting
sg_df.to_csv("stations.csv")
pd.read_csv("stations.csv")

Unnamed: 0                                       Neighborhood
0             0                                        Jurong East
1             1                                        Bukit Batok
2             2                                       Bukit Gombak
3             3                                          Brickland
4             4                                      Choa Chu Kang
5             5                                            Yew Tee
6             6                                       Sungei Kadut
7             7                                             Kranji
8             8                                          Marsiling
9             9                                          Woodlands
10           10                                          Admiralty
11           11                                          Sembawang
12           12                                           Canberra
13           13                                             Yishun
14           14                                             Khatib
15           15                                       Yio Chu Kang
16           16                                         Ang Mo Kio
17           17                                             Bishan
18           18                                           Braddell
19           19                                          Toa Payoh
20           20                                             Novena
21           21                                             Newton
22           22                                            Orchard
23           23                                           Somerset
24           24                                        Dhoby Ghaut
25           25                                          City Hall
26           26                                      Raffles Place
27           27                                         Marina Bay
28           28                                  Marina South Pier
29           29                                          Pasir Ris
30           30                                           Tampines
31           31                                              Simei
32           32                                        Tanah Merah
33           33                                              Bedok
34           34                                          Kembangan
35           35                                              Eunos
36           36                                         Paya Lebar
37           37                                           Aljunied
38           38                                            Kallang
39           39                                           Lavender
40           40                                              Bugis
41           41                                          City Hall
42           42                                      Raffles Place
43           43                                      Tanjong Pagar
44           44                                        Outram Park
45           45                                        Tiong Bahru
46           46                                            Redhill
47           47                                         Queenstown
48           48                                       Commonwealth
49           49                                        Buona Vista
50           50                                              Dover
51           51                                           Clementi
52           52                                        Jurong East
53           53                                     Chinese Garden
54           54                                           Lakeside
55           55                                           Boon Lay
56           56                                            Pioneer
57           57                                           Joo Koon
58           58                                     

#3. Gather information of each area

In [0]:
#Get the geographical coordinates

# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Singapore'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

# call the function to get the coordinates, store in a new list using list comprehension
coords = [get_latlng(neighborhood) for neighborhood in sg_df["Neighborhood"].tolist()]

coords

[[1.3343700000000354, 103.74367000000007],
 [1.349520000000041, 103.75277000000006],
 [1.3641700000000583, 103.75722000000007],
 [1.3735820121330484, 103.73892614503045],
 [1.3861600000000749, 103.74618000000004],
 [1.3944400000000314, 103.75389000000007],
 [1.4166700000000674, 103.73333000000008],
 [1.429110000000037, 103.75620000000004],
 [1.4411100000000374, 103.77083000000005],
 [1.4358500000000731, 103.78698000000009],
 [1.4406900000000746, 103.80093000000005],
 [1.4479400000000737, 103.81891000000007],
 [1.4448297193459918, 103.82796658849382],
 [1.4362100000000737, 103.83582000000007],
 [1.3534439970000562, 103.81650913600004],
 [1.3879700000000526, 103.86879000000005],
 [1.3716100000000324, 103.84546000000006],
 [1.3507900000000745, 103.85110000000009],
 [1.3433096560276077, 103.85357333378265],
 [1.3344800000000419, 103.85108000000008],
 [1.3191000000000486, 103.84372000000008],
 [1.312180000000069, 103.83912000000004],
 [1.3011200000000258, 103.83955000000009],
 [1.3024700000

In [0]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

# merge the coordinates into the original dataframe
sg_df['Latitude'] = df_coords['Latitude']
sg_df['Longitude'] = df_coords['Longitude']

# check the neighborhoods and the coordinates
print(sg_df.shape)
sg_df

(227, 3)


Neighborhood  Latitude   Longitude
0                                          Jurong East  1.334370  103.743670
1                                          Bukit Batok  1.349520  103.752770
2                                         Bukit Gombak  1.364170  103.757220
3                                            Brickland  1.373582  103.738926
4                                        Choa Chu Kang  1.386160  103.746180
5                                              Yew Tee  1.394440  103.753890
6                                         Sungei Kadut  1.416670  103.733330
7                                               Kranji  1.429110  103.756200
8                                            Marsiling  1.441110  103.770830
9                                            Woodlands  1.435850  103.786980
10                                           Admiralty  1.440690  103.800930
11                                           Sembawang  1.447940  103.818910
12                                            Canberra  1.444830  103.827967
13                                              Yishun  1.436210  103.835820
14                                              Khatib  1.353444  103.816509
15                                        Yio Chu Kang  1.387970  103.868790
16                                          Ang Mo Kio  1.371610  103.845460
17                                              Bishan  1.350790  103.851100
18                                            Braddell  1.343310  103.853573
19                                           Toa Payoh  1.334480  103.851080
20                                              Novena  1.319100  103.843720
21                                              Newton  1.312180  103.839120
22                                             Orchard  1.301120  103.839550
23                                            Somerset  1.302470  103.839170
24                                         Dhoby Ghaut  1.298740  103.848000
25                                           City Hall  1.292570  103.856870
26                                       Raffles Place  1.281890  103.849120
27                                          Marina Bay  1.281050  103.859720
28                                   Marina South Pier  1.270287  103.863150
29                                           Pasir Ris  1.371940  103.949940
30                                            Tampines  1.368190  103.929480
31                                               Simei  1.342900  103.954350
32                                         Tanah Merah  1.323500  103.941740
33                                               Bedok  1.324250  103.952970
34                                           Kembangan  1.322280  103.911350
35                                               Eunos  1.320840  103.899800
36                                          Paya Lebar  1.325030  103.890490
37                                            Aljunied  1.329278  103.879562
38                                             Kallang  1.333330  103.866670
39                                            Lavender  1.307170  103.863010
40                                               Bugis  1.300810  103.855910
41                                           City Hall  1.292570  103.856870
42                                       Raffles Place  1.281890  103.849120
43                                       Tanjong Pagar  1.278890  103.845390
44                                         Outram Park  1.282500  103.838060
45                                         Tiong Bahru  1.289530  103.832080
46                                             Redhill  1.287340  103.818840
47                                          Queenstown  1.299660  103.801720
48                                        Commonwealth  1.304791  103.797615
49                                         Buona Vista  1.280560  103.788060
50                                               Dover  1.314370  103.893460
51                                    

In [0]:
# save the DataFrame as CSV file
sg_df.to_csv("sg_df.csv", index=False)

In [0]:
#Create a map of Singapore with neighborhoods superimposed on top

# get the coordinates of Singapore
address = 'Bishan, Singapore'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Singapore {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Singapore 1.3514521, 103.8482496.


In [0]:
# create map of Toronto using latitude and longitude values
map_sg = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(sg_df['Latitude'], sg_df['Longitude'], sg_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_sg)  
    
map_sg

In [0]:
map_sg.save('map_sg.html')

In [0]:
# define your Foursquare Credentials and Version
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20200131' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET: ' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: E0SIWDOT1WPEOIHYILLTRUHS3ECZL2YBVPASE33Q42RBSTJO
CLIENT_SECRET: VFYMSNRMVA0CV3MFS55KVZJPAEGOFDIX2BB1G0DYUA0OVD4C


In [0]:
sg_df=sg_df.loc[:, ~sg_df.columns.str.contains('^Unnamed')]
print(sg_df.shape)
sg_df

(227, 3)


Neighborhood  Latitude   Longitude
0                                          Jurong East  1.334370  103.743670
1                                          Bukit Batok  1.349520  103.752770
2                                         Bukit Gombak  1.364170  103.757220
3                                            Brickland  1.373582  103.738926
4                                        Choa Chu Kang  1.386160  103.746180
5                                              Yew Tee  1.394440  103.753890
6                                         Sungei Kadut  1.416670  103.733330
7                                               Kranji  1.429110  103.756200
8                                            Marsiling  1.441110  103.770830
9                                            Woodlands  1.435850  103.786980
10                                           Admiralty  1.440690  103.800930
11                                           Sembawang  1.447940  103.818910
12                                            Canberra  1.444830  103.827967
13                                              Yishun  1.436210  103.835820
14                                              Khatib  1.353444  103.816509
15                                        Yio Chu Kang  1.387970  103.868790
16                                          Ang Mo Kio  1.371610  103.845460
17                                              Bishan  1.350790  103.851100
18                                            Braddell  1.343310  103.853573
19                                           Toa Payoh  1.334480  103.851080
20                                              Novena  1.319100  103.843720
21                                              Newton  1.312180  103.839120
22                                             Orchard  1.301120  103.839550
23                                            Somerset  1.302470  103.839170
24                                         Dhoby Ghaut  1.298740  103.848000
25                                           City Hall  1.292570  103.856870
26                                       Raffles Place  1.281890  103.849120
27                                          Marina Bay  1.281050  103.859720
28                                   Marina South Pier  1.270287  103.863150
29                                           Pasir Ris  1.371940  103.949940
30                                            Tampines  1.368190  103.929480
31                                               Simei  1.342900  103.954350
32                                         Tanah Merah  1.323500  103.941740
33                                               Bedok  1.324250  103.952970
34                                           Kembangan  1.322280  103.911350
35                                               Eunos  1.320840  103.899800
36                                          Paya Lebar  1.325030  103.890490
37                                            Aljunied  1.329278  103.879562
38                                             Kallang  1.333330  103.866670
39                                            Lavender  1.307170  103.863010
40                                               Bugis  1.300810  103.855910
41                                           City Hall  1.292570  103.856870
42                                       Raffles Place  1.281890  103.849120
43                                       Tanjong Pagar  1.278890  103.845390
44                                         Outram Park  1.282500  103.838060
45                                         Tiong Bahru  1.289530  103.832080
46                                             Redhill  1.287340  103.818840
47                                          Queenstown  1.299660  103.801720
48                                        Commonwealth  1.304791  103.797615
49                                         Buona Vista  1.280560  103.788060
50                                               Dover  1.314370  103.893460
51                                    

In [0]:
#Get the neighborhood's latitude and longitude values.
sg_df.loc[0, 'Neighborhood']
neighborhood_latitude = sg_df.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = sg_df.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = sg_df.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Jurong East are 1.3343700000000354, 103.74367000000007.


In [0]:
# type your answer here

LIMIT = 50 # limit of number of venues returned by Foursquare API
radius = 500
# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=E0SIWDOT1WPEOIHYILLTRUHS3ECZL2YBVPASE33Q42RBSTJO&client_secret=VFYMSNRMVA0CV3MFS55KVZJPAEGOFDIX2BB1G0DYUA0OVD4C&v=20200131&ll=1.3343700000000354,103.74367000000007&radius=500&limit=50'

In [0]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e438dcf006dce001b754d0c'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-51c0356c498e19c820f5e48e-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/apparel_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d103951735',
         'name': 'Clothing Store',
         'pluralName': 'Clothing Stores',
         'primary': True,
         'shortName': 'Apparel'}],
       'id': '51c0356c498e19c820f5e48e',
       'location': {'address': '#02-37 & #03-30, Jem',
        'cc': 'SG',
        'city': 'Singapore',
        'country': 'Singapore',
        'crossStreet': '50 Jurong Gateway Rd',
        'distance': 144,
        'formattedAddress': ['#02-37 & #03-30, Jem (50 Jurong Gateway Rd)',
         '608549',
         'Singapore'],
 

In [0]:
#function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [0]:
#Now, let's get the top 50 venues that are within a radius of 300 meters.

radius = 300
LIMIT = 50

venues = []

for lat, long, neighborhood in zip(sg_df['Latitude'], sg_df['Longitude'], sg_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(3989, 7)


Neighborhood  Latitude  Longitude  \
0  Jurong East   1.33437  103.74367   
1  Jurong East   1.33437  103.74367   
2  Jurong East   1.33437  103.74367   
3  Jurong East   1.33437  103.74367   
4  Jurong East   1.33437  103.74367   

                                           VenueName  VenueLatitude  \
0                                             UNIQLO       1.333175   
1                                          MUJI 無印良品       1.333187   
2                          Song Fa Bak Kut Teh 松發肉骨茶       1.333394   
3  Tonkatsu by Ma Maison とんかつ マメゾン (Tonkatsu by M...       1.333668   
4                                        Johan Paris       1.334083   

   VenueLongitude           VenueCategory  
0      103.743160          Clothing Store  
1      103.743064  Furniture / Home Store  
2      103.743420      Chinese Restaurant  
3      103.742818     Japanese Restaurant  
4      103.742384                  Bakery

In [0]:
print(venues_df.groupby(["Neighborhood"]).count().shape)
venues_df.groupby(["Neighborhood"]).count()

(178, 6)


Latitude  Longitude  \
Neighborhood                                                              
Admiralty                                                  4          4   
Aljunied                                                   5          5   
Ang Mo Kio                                                46         46   
Aviation Park                                              2          2   
Bahar Junction                                            19         19   
Bartley                                                    2          2   
Bayfront                                                  74         74   
Bayshore                                                   9          9   
Beauty World                                              50         50   
Bedok                                                      2          2   
Bedok North                                                4          4   
Bedok Reservoir                                            1          1   
Bedok South                                                1          1   
Bencoolen                                                 36         36   
Bendemeer                                                 13         13   
Bishan                                                    52         52   
Boon Keng                                                  9          9   
Boon Lay                                                   2          2   
Botanic Gardens • Kebun Bunga                             62         62   
Braddell                                                   4          4   
Bras Basah                                                34         34   
Brickland                                                  3          3   
Bright Hill                                                8          8   
Buangkok                                                   4          4   
Bugis                                                     82         82   
Bukit Batok                                                7          7   
Bukit Batok West                                           7          7   
Bukit Brown[c]                                             2          2   
Bukit Panjang                                              1          1   
Buona Vista                                               32         32   
Caldecott                                                  8          8   
Canberra                                                   3          3   
Cantonment                                                11         11   
Cashew                                                     8          8   
Changi Airport                                            86         86   
Changi Airport Terminal 5                                 50         50   
Changi Airport Terminal 5[d]                              50         50   
Chinatown                                                100        100   
Chinese Garden                                            25         25   
Choa Chu Kang                                             28         28   
Choa Chu Kang West                                        14         14   
City Hall                                                100        100   
Clarke Quay                                               45         45   
Clementi                                                  50         50   
Commonwealth                                               5          5   
Corporation                                                4          4   
Dakota                                                    24         24   
Defu                                                       1          1   
Dhoby Ghaut                                              132        132   
Dover                                                     35         35   
Downtown                                                  24         24   
Enterprise                                                13         13   
Es

#4. Analyze Neighborhoods

In [0]:
#Let's find out how many unique categories can be curated from all the returned venues
print('There are {} unique categories. \n'.format(len(venues_df['VenueCategory'].unique())))

# print out the list of categories
venues_df['VenueCategory'].unique()

There are 280 unique categories. 



array(['Clothing Store', 'Furniture / Home Store', 'Chinese Restaurant',
       'Japanese Restaurant', 'Bakery', 'Movie Theater', 'Multiplex',
       'Bookstore', 'Department Store', 'Trail', 'Shopping Mall',
       'Vegetarian / Vegan Restaurant', 'Supermarket',
       'Frozen Yogurt Shop', 'Indian Restaurant', 'Hotpot Restaurant',
       'Burger Joint', 'Accessories Store', 'Playground', 'Shoe Store',
       'Bubble Tea Shop', 'Salad Place', 'Ramen Restaurant',
       'German Restaurant', 'Coffee Shop', 'Halal Restaurant',
       'Sandwich Place', 'Sushi Restaurant', 'Sporting Goods Shop',
       'Dumpling Restaurant', 'Gym / Fitness Center', 'Café',
       'Cupcake Shop', 'Malay Restaurant', 'Fast Food Restaurant',
       'Dim Sum Restaurant', 'Food Court', 'Bus Station', 'Dessert Shop',
       'Dog Run', 'Park', 'Track', 'Thai Restaurant', 'Asian Restaurant',
       'Portuguese Restaurant', 'Italian Restaurant', 'Burrito Place',
       'Diner', 'Restaurant', 'Bus Stop', 'Cafeteria'

In [0]:
#Analyze Each Neighborhood

# one hot encoding
sg_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
sg_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [sg_onehot.columns[-1]] + list(sg_onehot.columns[:-1])
sg_onehot = sg_onehot[fixed_columns]

print(sg_onehot.shape)
sg_onehot.head()
#sg_onehot

(3989, 281)


Neighborhoods  Accessories Store  Airport  Airport Lounge  Airport Terminal  \
0   Jurong East                  0        0               0                 0   
1   Jurong East                  0        0               0                 0   
2   Jurong East                  0        0               0                 0   
3   Jurong East                  0        0               0                 0   
4   Jurong East                  0        0               0                 0   

   American Restaurant  Arcade  Argentinian Restaurant  Art Gallery  \
0                    0       0                       0            0   
1                    0       0                       0            0   
2                    0       0                       0            0   
3                    0       0                       0            0   
4                    0       0                       0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   

   Australian Restaurant  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                      0          0           0       0     0    0   
1                      0          0           0       0     0    0   
2                      0          0           0       0     0    0   
3                      0          0           0       0     0    0   
4                      0          0           0       1     0    0   

   Basketball Court  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                 0      0                0         0            0   
1                 0      0                0         0            0   
2                 0      0                0         0            0   
3                 0      0                0         0            0   
4                 0      0                0         0            0   

   Bike Rental / Bike Share  Bistro  Boarding House  Boat or Ferry  Bookstore  \
0                         0       0               0              0          0   
1                         0       0               0              0          0   
2                         0       0               0              0          0   
3                         0       0               0              0          0   
4                         0       0               0              0          0   

   Border Crossing  Botanical Garden  Boutique  Bowling Alley  Breakfast Spot  \
0                0                 0         0              0               0   
1                0                 0         0              0               0   
2                0                 0         0              0               0   
3                0                 0         0              0               0   
4                0                 0         0              0               0   

   Brewery  Bridge  Bubble Tea Shop  Buddhist Temple  Buffet  Building  \
0        0       0                0                0       0         0   
1        0       0                0                0       0         0   
2        0       0                0                0       0         0   
3        0       0                0                0       0         0   
4        0       0                0                0       0         0   

   Burger Joint  Burmese Restaurant  Burrito Place  Bus Line  Bus Station  \
0             0                   0              0         0            0   
1             0                   0              0         0            0   
2             0                   0              0         0            0   
3             0                   0              0         0            0   
4             0                   0              0       

In [0]:
# check if the results contain "Shopping Mall"
"Shopping Mall" in venues_df['VenueCategory'].unique()

True

In [0]:
#Let's find out how many unique Neighborhoods
print('There are {} unique Neighborhoods. \n'.format(len(sg_onehot['Neighborhoods'].unique())))

#Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

sg_grouped = sg_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(sg_grouped.shape)
sg_grouped

There are 178 unique Neighborhoods. 

(178, 281)


Neighborhoods  Accessories Store  \
0                                            Admiralty           0.000000   
1                                             Aljunied           0.000000   
2                                           Ang Mo Kio           0.000000   
3                                        Aviation Park           0.000000   
4                                       Bahar Junction           0.000000   
5                                              Bartley           0.000000   
6                                             Bayfront           0.054054   
7                                             Bayshore           0.000000   
8                                         Beauty World           0.000000   
9                                                Bedok           0.000000   
10                                         Bedok North           0.000000   
11                                     Bedok Reservoir           0.000000   
12                                         Bedok South           0.000000   
13                                           Bencoolen           0.000000   
14                                           Bendemeer           0.000000   
15                                              Bishan           0.000000   
16                                           Boon Keng           0.000000   
17                                            Boon Lay           0.000000   
18                       Botanic Gardens • Kebun Bunga           0.000000   
19                                            Braddell           0.000000   
20                                          Bras Basah           0.000000   
21                                           Brickland           0.000000   
22                                         Bright Hill           0.000000   
23                                            Buangkok           0.000000   
24                                               Bugis           0.000000   
25                                         Bukit Batok           0.000000   
26                                    Bukit Batok West           0.000000   
27                                      Bukit Brown[c]           0.000000   
28                                       Bukit Panjang           0.000000   
29                                         Buona Vista           0.000000   
30                                           Caldecott           0.000000   
31                                            Canberra           0.000000   
32                                          Cantonment           0.000000   
33                                              Cashew           0.000000   
34                                      Changi Airport           0.023256   
35                           Changi Airport Terminal 5           0.020000   
36                        Changi Airport Terminal 5[d]           0.020000   
37                                           Chinatown           0.000000   
38                                      Chinese Garden           0.000000   
39                                       Choa Chu Kang           0.000000   
40                                  Choa Chu Kang West           0.000000   
41                                           City Hall           0.000000   
42                                         Clarke Quay           0.000000   
43                                            Clementi           0.000000   
44                                        Commonwealth           0.000000   
45                                         Corporation           0.000000   
46                                              Dakota           0.000000   
47                                                Defu           0.000000   
48                                         Dhoby Ghaut           0.000000   
49                                               Dover           0.000000   
50                                            Downtown           0.000000   
51                                   

#5. Area with Shopping Mall

In [0]:
# filter column "Shopping Mall" for the stations that have shopping malls nearby

mall = sg_onehot.loc[sg_onehot['Shopping Mall'] > 0]
neighborhoods_with_mall = mall['Neighborhoods'].unique()

print('There are {} unique Neighborhoods with malls. \n'.format(len(neighborhoods_with_mall)))
#print('There are {} unique Neighborhoods with malls. \n'.format(len(sg_grouped[sg_grouped["Shopping Mall"] > 0])))
neighborhoods_with_mall

There are 39 unique Neighborhoods with malls. 



array(['Jurong East', 'Woodlands', 'Sembawang', 'Yio Chu Kang', 'Bishan',
       'Orchard', 'Somerset', 'City Hall', 'Pasir Ris', 'Simei', 'Bugis',
       'Buona Vista', 'Dover', 'Clementi', 'Chinese Garden', 'Expo',
       'HarbourFront',
       'Station code "NE2" is reserved for a possible future station.',
       'Little India', 'Hougang', 'Sengkang', 'Promenade',
       'Botanic Gardens • Kebun Bunga', 'Labrador Park',
       'Prince Edward Road', 'Hillview', 'Beauty World', 'Downtown',
       'Bencoolen', 'Woodlands North', 'Woodlands South', 'Great World',
       'Havelock', 'Maxwell', 'Shenton Way',
       "Founders' Memorial • Peringatan Pengasas", 'Jurong West',
       'Nanyang Gateway', 'Pasir Ris East'], dtype=object)

In [0]:
#Create a new DataFrame for Shopping Mall data only
print('There are {} unique Neighborhoods with malls (if Shopping Mall value is not 0). \n'.format((len(sg_grouped[sg_grouped["Shopping Mall"] > 0]))))
sg_mall = sg_grouped[["Neighborhoods","Shopping Mall"]]
sg_mall

#mall = sg_onehot.loc[sg_onehot['Shopping Mall'] > 0]
#neighborhoods_with_mall = mall['Neighborhoods'].unique()

There are 39 unique Neighborhoods with malls (if Shopping Mall value is not 0). 



Neighborhoods  Shopping Mall
0                                            Admiralty       0.000000
1                                             Aljunied       0.000000
2                                           Ang Mo Kio       0.000000
3                                        Aviation Park       0.000000
4                                       Bahar Junction       0.000000
5                                              Bartley       0.000000
6                                             Bayfront       0.000000
7                                             Bayshore       0.000000
8                                         Beauty World       0.020000
9                                                Bedok       0.000000
10                                         Bedok North       0.000000
11                                     Bedok Reservoir       0.000000
12                                         Bedok South       0.000000
13                                           Bencoolen       0.027778
14                                           Bendemeer       0.000000
15                                              Bishan       0.038462
16                                           Boon Keng       0.000000
17                                            Boon Lay       0.000000
18                       Botanic Gardens • Kebun Bunga       0.064516
19                                            Braddell       0.000000
20                                          Bras Basah       0.000000
21                                           Brickland       0.000000
22                                         Bright Hill       0.000000
23                                            Buangkok       0.000000
24                                               Bugis       0.048780
25                                         Bukit Batok       0.000000
26                                    Bukit Batok West       0.000000
27                                      Bukit Brown[c]       0.000000
28                                       Bukit Panjang       0.000000
29                                         Buona Vista       0.062500
30                                           Caldecott       0.000000
31                                            Canberra       0.000000
32                                          Cantonment       0.000000
33                                              Cashew       0.000000
34                                      Changi Airport       0.000000
35                           Changi Airport Terminal 5       0.000000
36                        Changi Airport Terminal 5[d]       0.000000
37                                           Chinatown       0.000000
38                                      Chinese Garden       0.040000
39                                       Choa Chu Kang       0.000000
40                                  Choa Chu Kang West       0.000000
41                                           City Hall       0.040000
42                                         Clarke Quay       0.000000
43                                            Clementi       0.040000
44                                        Commonwealth       0.000000
45                                         Corporation       0.000000
46                                              Dakota       0.000000
47                                                Defu       0.000000
48                                         Dhoby Ghaut       0.000000
49                                               Dover       0.114286
50                                            Downtown       0.041667
51                                          Enterprise       0.000000
52                                           Esplanade       0.000000
53                                               Eunos       0.000000
54                                                Expo       0.027027
55                                         Farrer Park       0.000000
56                                         Farrer R

#6. k-means clustering

In [0]:
#Cluster Neighborhoods
#Run k-means to cluster the neighborhoods in Singapore into 3 clusters.

# set number of clusters
kclusters = 3

sg_clustering = sg_mall.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(sg_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:100]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0,
       0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1,
       0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0,
       0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [0]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
sg_merged = sg_mall.copy()

# add clustering labels
sg_merged["Cluster Labels"] = kmeans.labels_

sg_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
#sg_merged.head()
sg_merged

Neighborhood  Shopping Mall  \
0                                            Admiralty       0.000000   
1                                             Aljunied       0.000000   
2                                           Ang Mo Kio       0.000000   
3                                        Aviation Park       0.000000   
4                                       Bahar Junction       0.000000   
5                                              Bartley       0.000000   
6                                             Bayfront       0.000000   
7                                             Bayshore       0.000000   
8                                         Beauty World       0.020000   
9                                                Bedok       0.000000   
10                                         Bedok North       0.000000   
11                                     Bedok Reservoir       0.000000   
12                                         Bedok South       0.000000   
13                                           Bencoolen       0.027778   
14                                           Bendemeer       0.000000   
15                                              Bishan       0.038462   
16                                           Boon Keng       0.000000   
17                                            Boon Lay       0.000000   
18                       Botanic Gardens • Kebun Bunga       0.064516   
19                                            Braddell       0.000000   
20                                          Bras Basah       0.000000   
21                                           Brickland       0.000000   
22                                         Bright Hill       0.000000   
23                                            Buangkok       0.000000   
24                                               Bugis       0.048780   
25                                         Bukit Batok       0.000000   
26                                    Bukit Batok West       0.000000   
27                                      Bukit Brown[c]       0.000000   
28                                       Bukit Panjang       0.000000   
29                                         Buona Vista       0.062500   
30                                           Caldecott       0.000000   
31                                            Canberra       0.000000   
32                                          Cantonment       0.000000   
33                                              Cashew       0.000000   
34                                      Changi Airport       0.000000   
35                           Changi Airport Terminal 5       0.000000   
36                        Changi Airport Terminal 5[d]       0.000000   
37                                           Chinatown       0.000000   
38                                      Chinese Garden       0.040000   
39                                       Choa Chu Kang       0.000000   
40                                  Choa Chu Kang West       0.000000   
41                                           City Hall       0.040000   
42                                         Clarke Quay       0.000000   
43                                            Clementi       0.040000   
44                                        Commonwealth       0.000000   
45                                         Corporation       0.000000   
46                                              Dakota       0.000000   
47                                                Defu       0.000000   
48                                         Dhoby Ghaut       0.000000   
49                                               Dover       0.114286   
50                                            Downtown       0.041667   
51                                          Enterprise       0.000000   
52                                           Esplanade       0.000000   
53                                               Eunos       0.000000   
54                         

In [0]:
# merge sg_grouped with sg_data to add latitude/longitude for each neighborhood
sg_merged = sg_merged.join(sg_df.set_index("Neighborhood"), on="Neighborhood")

print(sg_merged.shape)
sg_merged.head() # check the last columns!

(216, 5)


Neighborhood  Shopping Mall  Cluster Labels  Latitude   Longitude
0      Admiralty            0.0               0  1.440690  103.800930
1       Aljunied            0.0               0  1.329278  103.879562
2     Ang Mo Kio            0.0               0  1.371610  103.845460
2     Ang Mo Kio            0.0               0  1.371610  103.845460
3  Aviation Park            0.0               0  1.365267  104.015240

In [0]:
# sort the results by Cluster Labels
print(sg_merged.shape)
sg_merged.sort_values(["Cluster Labels"], inplace=True)
sg_merged

(216, 5)


Neighborhood  Shopping Mall  \
0                                            Admiralty       0.000000   
99                                      Marine Terrace       0.000000   
100                                          Marsiling       0.000000   
101                                          Marymount       0.000000   
102                                             Mattar       0.000000   
104                                          Mayflower       0.000000   
105                                        Mountbatten       0.000000   
106                                   Nanyang Crescent       0.000000   
108                                             Napier       0.000000   
109                                             Newton       0.000000   
98                                       Marine Parade       0.000000   
109                                             Newton       0.000000   
111                                             Novena       0.000000   
113                                  Orchard Boulevard       0.000000   
114                                        Outram Park       0.000000   
114                                        Outram Park       0.000000   
114                                        Outram Park       0.000000   
115                                      Pasir Panjang       0.000000   
118                                         Paya Lebar       0.000000   
118                                         Paya Lebar       0.000000   
119                                     Peng Kang Hill       0.000000   
110                                     Nicoll Highway       0.000000   
120                                            Pioneer       0.000000   
97                                   Marina South Pier       0.000000   
95                                          Marina Bay       0.000000   
78                                             Kallang       0.000000   
79                                         Katong Park       0.000000   
80                                           Kembangan       0.000000   
81                                          Kent Ridge       0.000000   
82                                              Keppel       0.000000   
83                                              Khatib       0.000000   
84                                    King Albert Park       0.000000   
85                                               Kovan       0.000000   
176                                             Yishun       0.000000   
96                                        Marina South       0.000000   
88                                            Lakeside       0.000000   
90                                              Lentor       0.000000   
91                                        Little India       0.022727   
91                                        Little India       0.022727   
92                                        Lorong Chuan       0.000000   
93                                              Loyang       0.000000   
94                                          MacPherson       0.000000   
94                                          MacPherson       0.000000   
95                                          Marina Bay       0.000000   
95                                          Marina Bay       0.000000   
89                                            Lavender       0.000000   
121                                       Potong Pasir       0.000000   
124                                            Punggol       0.000000   
125                                      Punggol Coast       0.000000   
152                                        Tanjong Rhu       0.000000   
153                                              Tawas       0.000000   
154                                          Teck Ghee       0.000000   
155                                         Telok Ayer       0.000000   
156                                      Telok Blangah       0.000000   
157                        

In [0]:
#Finally, let's visualize the resulting clusters

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(sg_merged['Latitude'], sg_merged['Longitude'], sg_merged['Neighborhood'], sg_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [0]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

#7. Examine Clusters

In [0]:
#Cluster 0
sg_merged.loc[sg_merged['Cluster Labels'] == 0]

Neighborhood  Shopping Mall  Cluster Labels  \
0                                  Admiralty       0.000000               0   
99                            Marine Terrace       0.000000               0   
100                                Marsiling       0.000000               0   
101                                Marymount       0.000000               0   
102                                   Mattar       0.000000               0   
104                                Mayflower       0.000000               0   
105                              Mountbatten       0.000000               0   
106                         Nanyang Crescent       0.000000               0   
108                                   Napier       0.000000               0   
109                                   Newton       0.000000               0   
98                             Marine Parade       0.000000               0   
109                                   Newton       0.000000               0   
111                                   Novena       0.000000               0   
113                        Orchard Boulevard       0.000000               0   
114                              Outram Park       0.000000               0   
114                              Outram Park       0.000000               0   
114                              Outram Park       0.000000               0   
115                            Pasir Panjang       0.000000               0   
118                               Paya Lebar       0.000000               0   
118                               Paya Lebar       0.000000               0   
119                           Peng Kang Hill       0.000000               0   
110                           Nicoll Highway       0.000000               0   
120                                  Pioneer       0.000000               0   
97                         Marina South Pier       0.000000               0   
95                                Marina Bay       0.000000               0   
78                                   Kallang       0.000000               0   
79                               Katong Park       0.000000               0   
80                                 Kembangan       0.000000               0   
81                                Kent Ridge       0.000000               0   
82                                    Keppel       0.000000               0   
83                                    Khatib       0.000000               0   
84                          King Albert Park       0.000000               0   
85                                     Kovan       0.000000               0   
176                                   Yishun       0.000000               0   
96                              Marina South       0.000000               0   
88                                  Lakeside       0.000000               0   
90                                    Lentor       0.000000               0   
91                              Little India       0.022727               0   
91                              Little India       0.022727               0   
92                              Lorong Chuan       0.000000               0   
93                                    Loyang       0.000000               0   
94                                MacPherson       0.000000               0   
94                                MacPherson       0.000000               0   
95                                Marina Bay       0.000000               0   
95                                Marina Bay       0.000000               0   
89                                  Lavender       0.000000               0   
121                             Potong Pasir       0.000000               0   
124                                  Punggol       0.000000               0   
125                            Punggol Coast       0.000000               0   
152                              Tanjong Rhu       0.000000               0   
153

In [0]:
#Cluster 1
sg_merged.loc[sg_merged['Cluster Labels'] == 1]

Neighborhood  Shopping Mall  \
15                                              Bishan       0.038462   
64                                        HarbourFront       0.040000   
13                                           Bencoolen       0.027778   
64                                        HarbourFront       0.040000   
112                                            Orchard       0.060000   
117                                     Pasir Ris East       0.041667   
87                                       Labrador Park       0.047619   
67                                            Hillview       0.052632   
116                                          Pasir Ris       0.041667   
69                                             Hougang       0.076923   
116                                          Pasir Ris       0.041667   
15                                              Bishan       0.038462   
41                                           City Hall       0.040000   
72                                         Jurong East       0.040000   
169                                          Woodlands       0.041667   
169                                          Woodlands       0.041667   
170                                    Woodlands North       0.041667   
171                                    Woodlands South       0.041667   
72                                         Jurong East       0.040000   
72                                         Jurong East       0.040000   
41                                           City Hall       0.040000   
175                                       Yio Chu Kang       0.076923   
69                                             Hougang       0.076923   
112                                            Orchard       0.060000   
49                                               Dover       0.114286   
107                                    Nanyang Gateway       0.035714   
50                                            Downtown       0.041667   
130                                          Sembawang       0.083333   
131                                           Sengkang       0.035714   
134                                        Shenton Way       0.050000   
29                                         Buona Vista       0.062500   
136                                              Simei       0.040000   
29                                         Buona Vista       0.062500   
138                                           Somerset       0.080000   
54                                                Expo       0.027027   
62                                         Great World       0.027027   
141  Station code "NE2" is reserved for a possible ...       0.064516   
54                                                Expo       0.027027   
43                                            Clementi       0.040000   
24                                               Bugis       0.048780   
123                                          Promenade       0.029412   
123                                          Promenade       0.029412   
122                                 Prince Edward Road       0.066667   
58            Founders' Memorial • Peringatan Pengasas       0.064516   
38                                      Chinese Garden       0.040000   
18                       Botanic Gardens • Kebun Bunga       0.064516   
18                       Botanic Gardens • Kebun Bunga       0.064516   
54                                                Expo       0.027027   
24                                               Bugis       0.048780   

     Cluster Labels  Latitude   Longitude  
15                1  1.350790  103.851100  
64                1  1.265200  103.820100  
13                1  1.301634  103.853344  
64                1  1.265200  103.820100  
112               1  1.301120  103.839550  
117               1  1.371940  103.949940  
87                1  1.272020  103.802260  
67                1  1.362155  103.7658

In [0]:
#Cluster 2
sg_merged.loc[sg_merged['Cluster Labels'] == 2]

Neighborhood  Shopping Mall  Cluster Labels  Latitude   Longitude
103      Maxwell           0.25               2  1.275088  103.849616

Observations:
<br>Most of the shopping malls are concentrated in the city at the South area of Singapore, with the highest number in cluster 2 and moderate number in cluster 1. 

On the other hand, cluster 0 has very few to no shopping mall near the train stations. This represents a great opportunity and high potential areas to open new cafes as there is very little to no competition from existing malls, which typically would have coffee chains and fastfood outlets to serve the needs. 

Meanwhile, shops in cluster 2 are likely suffering from intense competition due to oversupply and high concentration of shopping malls. From a business perspective, a cafe startup should not choose this area unless the cafe has extremely appealing Unique Selling Point. From another perspective, we can also visually observe the higher concentration of shopping malls in the central to southern area of the country, which signifies the key office areas that coincides with the Central Business District having the most number of people on average daily. 

Therefore, this project recommends business owners who want to open a cafe to tap on these findings to select a location that fits their cafe's target segment in cluster 1 with moderate competition, yet benefitting from the convenience and traffic of being close to a mall. 

Cafe owners with unique themes or menu can also open at the areas in cluster 0 with minimal competitions and gain first-mover advantage at the neighborhood. 

Lastly, this finding can also help business owners who are experiencing intense competition at cluster 2 to find alternatives for relocation in other area.